In [6]:
import numpy as np
import pandas as pd
import random
import json
import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import nltk
from nltk.stem.porter import PorterStemmer

## NLTK UTILS

In [7]:
stemmer = PorterStemmer()
def tokenize(sentence):
    return nltk.word_tokenize(sentence)
def stem(word):
    return stemmer.stem(word.lower())
def bag_of_words(tokenized_sentence, words):
    sentence_words = [stem(word) for word in tokenized_sentence]
    bag = np.zeros(len(words), dtype = np.float32)
    for idx, w in enumerate(words):
        if w in sentence_words:
            bag[idx] = 1
    return bag

## Model

In [8]:
class NeuralNet(nn.Module):
    def __init__(self, input_size, hidden_size, num_classes):
        super(NeuralNet, self).__init__()
        self.l1 = nn.Linear(input_size, hidden_size)
        self.l2 = nn.Linear(input_size, hidden_size)
        self.l3 = nn.Linear(input_size, hidden_size)
        self.output = nn.Linear(hidden_size, num_classes)
        self.relu = nn.ReLU()
    def forward(self, x):
        out = self.l1(x)
        out = self.relu(out)
        out = self.l2(out)
        out = self.relu(out)
        out = self.l3(out)
        out = self.output(out) #
        return out

In [9]:
with open('intents.json', 'r', encoding='utf8') as f:
    intents = json.load(f)

In [10]:
intents

{'intents': [{'tags': 'greeting',
   'patterns': ['Hi',
    'Hello',
    'Namaste',
    'Hey',
    'How are you?',
    'Are you there?',
    'Is anyone here?'],
   'responses': ['Hello, Thanks for Visiting DigiLocker',
    'Namaste, Welcome to DigiSaathi',
    'Hi DigiSaathi is here, How can I help?'],
   'context_set': ''},
  {'tags': 'goodbye',
   'patterns': ['Bye', 'See you later', 'Goodbye'],
   'responses': ['See you later', 'Thanks for Visiting', 'Have a nice Day']},
  {'tags': 'thanks',
   'patterns': ['Thanks', 'Thank you', "That's helpful"],
   'responses': ['Happy to help!', 'Any time!', 'My pleasure']},
  {'tags': 'access',
   'patterns': ['What URLs can be used to access DigiLocker?'],
   'responses': ['DigiLocker can be accessed at https://digilocker.gov.in'],
   'context_set': ''},
  {'tags': 'components',
   'patterns': ['What are the key components of DigiLocker?'],
   'responses': ['DigiLocker account has the following sections:\n Home –  This is the home screen of yo

In [11]:
all_words = []
tags = []
xy = []

In [12]:
for i in intents['intents']:
    tag = i['tags']
    tags.append(tag)
    for j in i['patterns']:
        w = tokenize(j)
        all_words.extend(w)
        xy.append((w, tag))

In [13]:
ignore_words = ['?','.','&',"'",'!','(',')',',','-']
all_words = [stem(w) for w in all_words if w not in ignore_words]
all_words = sorted(set(all_words))
tags = sorted(set(tags))

In [14]:
print(len(xy), "Patterns")
print(len(tags), "Tags:", tags)
print(len(all_words), "Unique Stemmed Words:", all_words)

50 Patterns
29 Tags: ['aadhaar', 'access', 'account', 'already', 'components', 'driving', 'files', 'foreign', 'forgot', 'goodbye', 'greeting', 'ilnkaadhar', 'integration', 'issuer', 'license', 'marksheet', 'message', 'otp', 'process', 'profile', 'security', 'signup', 'size', 'thanks', 'update', 'updatemobile', 'upload', 'uri', 'username']
199 Unique Stemmed Words: ["'aadhaar", "'no", "'s", "'the", "'thi", "'uid", '/request', '5', 'a', 'aadhaar', 'abl', 'about', 'access', 'account', 'after', 'again', 'allow', 'alreadi', 'am', 'an', 'and', 'ani', 'anyon', 'are', 'as', 'avail', 'be', 'becom', 'benefit', 'but', 'by', 'bye', 'can', 'cbse', 'certif', 'chang', 'check', 'citizen', 'compon', 'could', 'data', 'databas', 'detail', 'did', 'digilock', 'digit', 'display', 'dl', 'dl/rc', 'do', 'dob', 'document', 'doe', 'done', 'drive', 'dure', 'e-kyc', 'eaadhaar', 'email', 'enter', 'error', 'etc', 'explain', 'fetch', 'field', 'file', 'fill', 'follow', 'for', 'foreign', 'forgotten', 'frequent', 'get',

In [15]:
x_train = []
y_train = []
for (pattern_sentence, tag) in xy:
    bag = bag_of_words(pattern_sentence, all_words)
    x_train.append(bag)
    label = tags.index(tag)
    y_train.append(label)
x_train = np.array(x_train)
y_train = np.array(y_train)

In [16]:
num_epochs = 1000
batch_size = 8
learning_rate = 0.0002
input_size = len(x_train[0])
hidden_size = 199
output_size = len(tags)
print(input_size, output_size)

199 29


In [17]:
class ChatDataset(Dataset):
    def __init__(self):
        self.n_samples = len(x_train)
        self.x_data = x_train
        self.y_data = y_train
    def __getitem__(self, index):
        return self.x_data[index], self.y_data[index]
    def __len__(self):
        return self.n_samples

dataset = ChatDataset()
train_loader = DataLoader(dataset=dataset, batch_size=batch_size, shuffle=True, num_workers=0)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model = NeuralNet(input_size, hidden_size, output_size).to(device)

criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr= learning_rate)

for epoch in range(num_epochs):
    for (words, labels) in train_loader:
        words = words.to(device)
        labels = labels.to(dtype=torch.long).to(device)
        outputs = model(words)
        loss= criterion(outputs, labels)
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

    if(epoch+1)%100 == 0:
        print(f'Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}')
print(f'Final Loss: {loss.item():.4f}')

Epoch [100/1000], Loss: 0.0980
Epoch [200/1000], Loss: 0.0013
Epoch [300/1000], Loss: 0.0009
Epoch [400/1000], Loss: 0.0007
Epoch [500/1000], Loss: 0.0002
Epoch [600/1000], Loss: 0.0002
Epoch [700/1000], Loss: 0.3743
Epoch [800/1000], Loss: 0.0002
Epoch [900/1000], Loss: 0.0017
Epoch [1000/1000], Loss: 0.0001
Final Loss: 0.0001


In [18]:
data= {
    'model_state':model.state_dict(),
    'input_size':input_size,
    'hidden_size':hidden_size,
    'output_size':output_size,
    'all_words':all_words,
    'tags':tags
}

In [19]:
FILE = 'data.pth'
torch.save(data, FILE)
print(f'Training Complete. File Saved to {FILE}')

Training Complete. File Saved to data.pth


## CHAT

In [20]:
data = torch.load(FILE)

In [21]:
model_state = data['model_state']
model_state

OrderedDict([('l1.weight',
              tensor([[-0.0595, -0.0791, -0.0498,  ..., -0.0142,  0.0017,  0.0341],
                      [ 0.0151,  0.0171, -0.0126,  ...,  0.0571,  0.0771, -0.0210],
                      [ 0.0464,  0.0465, -0.0368,  ...,  0.0185, -0.0010,  0.0290],
                      ...,
                      [-0.0595,  0.0401, -0.0220,  ..., -0.0087, -0.0917,  0.1449],
                      [-0.0447, -0.0594, -0.0077,  ..., -0.0419,  0.0027, -0.0273],
                      [ 0.0052, -0.0240, -0.0009,  ..., -0.0252, -0.0161, -0.0339]])),
             ('l1.bias',
              tensor([ 1.2294e-01,  1.4685e-01,  4.8549e-02,  1.5489e-01,  1.0826e-01,
                       1.0325e-01, -1.2933e-02, -2.4994e-02,  1.4274e-01,  4.9784e-02,
                       1.0406e-01,  3.3593e-02,  1.2537e-01,  1.3319e-01,  9.2162e-02,
                       1.7593e-02,  3.4063e-02,  2.3401e-02,  5.9898e-02,  1.5092e-01,
                       7.5954e-02,  8.6649e-02,  1.3953e-01,  3.89

In [22]:
model = NeuralNet(input_size, hidden_size, output_size).to(device)
model.load_state_dict(model_state)
model.eval()

NeuralNet(
  (l1): Linear(in_features=199, out_features=199, bias=True)
  (l2): Linear(in_features=199, out_features=199, bias=True)
  (l3): Linear(in_features=199, out_features=199, bias=True)
  (output): Linear(in_features=199, out_features=29, bias=True)
  (relu): ReLU()
)

In [23]:
bot_name = "DigiSaathi"
print('Hi! Welcome to DigiSaathi.')
# print('Press 1 to get issued documents.')
# print('Press 2 to get chat support')
while True:
    sentence = input("You: ")
    if(sentence == "quit"):
        break
    sentence = tokenize(sentence)
    # print(f'Tokenized-{sentence}')
    X = bag_of_words(sentence, all_words)
    # if(1 in X):
    #     print('huihui')
    X = X.reshape(1, X.shape[0])
    X = torch.from_numpy(X).to(device)
    # print(f'X pt2-{X}')
    output = model(X)
    # print(f'OUTPUT-{output}')
    _, predicted = torch.max(output, dim=1)
    # print(f'PREDICTED- {predicted}')
    tag = tags[predicted.item()]
    # print(f'TAG-{tag}')
    probs = torch.softmax(output, dim=1)
    prob = probs[0][predicted.item()]
    # print(f'prob-{prob}')
    if prob.item() > 0.75:
        # print(prob.item())
        # print(f'tag:{tag}')
        for intent in intents['intents']:
            if tag == intent['tags']:
                print(f'{bot_name}: {random.choice(intent['responses'])}')
                break
    else:
        # print(prob.item())
        # for intent in intents['intents']:
        #     if tag == intent['tags']:
        #         print(f'Error Response: {random.choice(intent['responses'])}')
        print(f'{bot_name}: Sorry, I am not sure if I got that. Could you please try rephrasing your question?')
    print('-------------------------------------------------------------------------------------')

Hi! Welcome to DigiSaathi.


You:  quit
